# ASSOCIATION RULE MINING USING FP-GROWTH ALGORITHM

**Reading the Dataset**

In [1]:
import pandas as pd

df = pd.read_excel('Online Retail.xlsx')
df

InvoiceNo StockCode                          Description  Quantity  \
0         536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1         536365     71053                  WHITE METAL LANTERN         6   
2         536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3         536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4         536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   
...          ...       ...                                  ...       ...   
541904    581587     22613          PACK OF 20 SPACEBOY NAPKINS        12   
541905    581587     22899         CHILDREN'S APRON DOLLY GIRL          6   
541906    581587     23254        CHILDRENS CUTLERY DOLLY GIRL          4   
541907    581587     23255      CHILDRENS CUTLERY CIRCUS PARADE         4   
541908    581587     22138        BAKING SET 9 PIECE RETROSPOT          3   

                      InvoiceDate  UnitPrice  CustomerID         Country  
0      2010-12-01 08:26:00.000001       2.55     17850.0  United Kingdom  
1      2010-12-01 08:26:00.000001       3.39     17850.0  United Kingdom  
2      2010-12-01 08:26:00.000001       2.75     17850.0  United Kingdom  
3      2010-12-01 08:26:00.000001       3.39     17850.0  United Kingdom  
4      2010-12-01 08:26:00.000001       3.39     17850.0  United Kingdom  
...                           ...        ...         ...             ...  
541904 2011-12-09 12:49:59.999998       0.85     12680.0          France  
541905 2011-12-09 12:49:59.999998       2.10     12680.0          France  
541906 2011-12-09 12:49:59.999998       4.15     12680.0          France  
541907 2011-12-09 12:49:59.999998       4.15     12680.0          France  
541908 2011-12-09 12:49:59.999998       4.95     12680.0          France  

[541909 rows x 8 columns]

**Data Preprocessing**

In [2]:
dataframe = df[['InvoiceNo','StockCode']].groupby('InvoiceNo')['StockCode'].apply(list).reset_index(name='ItemSet')
dataset = []
for x in dataframe.ItemSet:
    dataset.append(list(set(x)))
for itemset in dataset:
    for i in range(len(itemset)):
        itemset[i] = str(itemset[i])

**Data Structure of a Tree Node**

In [3]:
class TreeNode:
    def __init__(self,item,count,parent):
        self.item = item
        self.count = count
        self.parent = parent
        self.next = None
        self.children = {}

**Functions used in Building the FP-Tree**

In [4]:
def Build_FP_Tree(dataset,counts,support):
    L = {}
    for a,b in zip(dataset,counts):
        for x in a:
            if x not in L:
                L[x] = 0
            L[x] += b
    L = {x:L[x] for x in L if L[x]>=support}
    header_table = {x:[L[x], None] for x in L}
    if header_table == {}:
        return None,None
    Tree = TreeNode(None,None,None)
    for a,b in zip(dataset,counts):
        ordered_set = [x for x in a if x in L]
        ordered_set.sort(key=lambda x:L[x],reverse=True)
        currentNode = Tree
        for x in ordered_set:
            currentNode = insert_tree(x,currentNode,header_table,b)
    return Tree,header_table

In [5]:
def insert_tree(item,treenode,header_table,count):
    if item in treenode.children:
        treenode.children[item].count += count
    else:
        newNode = TreeNode(item,count,treenode)
        treenode.children[item] = newNode
        insert_header_table(item,newNode,header_table)
    return treenode.children[item]

In [6]:
def insert_header_table(item,newNode,header_table):
    if header_table[item][1] == None:
        header_table[item][1] = newNode
    else:
        currentNode = header_table[item][1]
        while currentNode.next != None:
            currentNode = currentNode.next
        currentNode.next = newNode

**Functions used in Mining of the FP-Tree to Get Frequent Patterns**

In [7]:
def FP_growth(header_table,support,prefix_pattern,frequent_itemsets):
    ordered_itemlist = [x[0] for x in sorted(list(header_table.items()), key=lambda item:item[1][0])]
    for x in ordered_itemlist:
        conditional_frequent_set = set(prefix_pattern)
        conditional_frequent_set.add(x)
        frequent_itemsets[frozenset(conditional_frequent_set)] = header_table[x][0]
        conditional_pattern_base, count = get_conditional_pattern(x, header_table)
        conditional_FP_tree, conditional_header_table = Build_FP_Tree(conditional_pattern_base,count,support)
        if conditional_header_table != None:
            FP_growth(conditional_header_table,support,conditional_frequent_set,frequent_itemsets)

In [8]:
def get_conditional_pattern(item, header_table):
    node = header_table[item][1]
    conditional_pattern = []
    count = []
    while node != None:
        prefix_path = get_prefix_path(node)
        if len(prefix_path)>1:
            conditional_pattern.append(prefix_path[1:])
            count.append(node.count)
        node = node.next
    return conditional_pattern,count

In [9]:
def get_prefix_path(treenode):
    prefix_path = []
    while treenode.parent != None:
        prefix_path.append(treenode.item)
        treenode = treenode.parent
    return prefix_path

**Function to Generate Association Rules from Frequent-Pattern Set**

In [10]:
import itertools

def Association_Rules(frequent_pattern,length_dataset,confidence = 0.5, min_size = 2):
    association_rules = []
    for x in frequent_pattern:
        if len(x)>= min_size:
            for k in range(1,len(x)):
                s = list(map(frozenset, itertools.combinations(x,k)))
                for p in s:
                    conf = frequent_pattern[x]/frequent_pattern[p]
                    if conf >= confidence:
                        association_rules.append([set(p), set(x-p), frequent_pattern[x]/length_dataset, conf])
    return association_rules

**Function to Build the FP-Tree and Header Table, Mine the FP-Tree to Get Frequent Pattern Sets and Generate Association Rules**

In [11]:
def FP_Growth_Runner(dataset,support,conf):
    counts  = [1 for i in range(len(dataset))]
    tree,header = Build_FP_Tree(dataset,counts,support*len(dataset))
    if tree == None:
        print('No Frequent pattern for given dataset at support =',support)
        return None,{},[]
    frequent_pattern = {}
    FP_growth(header,support*len(dataset),set(),frequent_pattern)
    association_rules = Association_Rules(frequent_pattern,len(dataset),confidence = conf)
    return tree,frequent_pattern,association_rules

**Generate the FP-Tree, Frequent Patterns and Association Rules (*Change Support and Confidence in this Cell*)**

In [12]:
support = 0.025 #Change Support Here
confidence = 0.4 #Change Confidence Here
FPTree, frequent_patterns, assoc_rules = FP_Growth_Runner(dataset,support,confidence)

***FP-TREE***

In [14]:
from treelib import Tree

def create_visual_tree(FPTree,VT):
    VT.create_node('{'+f'{FPTree.item}:{FPTree.count}'+'}',str(FPTree),parent = None if FPTree.parent == None else str(FPTree.parent))
    for x in FPTree.children:
        create_visual_tree(FPTree.children[x],VT)

if FPTree != None:
    print('The FP-Tree for given dataset with support =',support)
    visual_tree = Tree()
    create_visual_tree(FPTree,visual_tree)
    print("Please check file 'Output_Tree.txt' for created FP-Tree\n")
    visual_tree.save2file('Output_Tree.txt',line_type='ascii-exr')
    visual_tree.show(line_type='ascii-exr')

The FP-Tree for given dataset with support = 0.025
Please check file 'Output_Tree.txt' for created FP-Tree

{None:None}
├── {20685:49}
│   ├── {20713:1}
│   ├── {79321:1}
│   ├── {82484:1}
│   ╰── {84380:1}
│       ╰── {84378:1}
│           ╰── {22551:1}
│               ╰── {22966:1}
├── {20712:10}
│   ├── {20719:1}
│   │   ╰── {23344:1}
│   ├── {21733:1}
│   │   ╰── {20723:1}
│   ├── {21928:1}
│   │   ╰── {22467:1}
│   ├── {22090:1}
│   │   ╰── {22326:1}
│   ├── {22326:1}
│   │   ╰── {22907:1}
│   ├── {22356:1}
│   ╰── {22467:1}
├── {20713:25}
├── {20719:14}
│   ├── {20723:1}
│   ├── {22554:1}
│   ├── {22558:4}
│   │   ├── {20685:1}
│   │   ╰── {22467:3}
│   ├── {22910:1}
│   │   ╰── {22728:1}
│   │       ╰── {79321:1}
│   ╰── {23207:1}
├── {20723:3}
├── {20724:49}
│   ├── {20719:4}
│   │   ├── {20723:1}
│   │   ╰── {21166:1}
│   │       ╰── {20723:1}
│   ├── {20723:2}
│   ├── {20914:1}
│   │   ╰── {21181:1}
│   ├── {21034:1}
│   │   ╰── {22356:1}
│   │       ╰── {20723:1}
│   ├── {21

***FREQUENT PATTERNS***

In [15]:
freq_pat = list(frequent_patterns.items())
supp = [x[1]/len(dataset) for x in freq_pat]
freq_pat = pd.DataFrame(freq_pat,columns = ['Frequent Pattern','Frequency'])
supp = pd.DataFrame(supp,columns = ['Support'])
freq_pat = pd.concat([freq_pat,supp],axis=1)
print('Frequent patterns for given dataset with support =',support)
freq_pat

Frequent patterns for given dataset with support = 0.025


Frequent Pattern  Frequency   Support
0            (22114)        652  0.025174
1            (22969)        654  0.025251
2            (22835)        663  0.025598
3            (21213)        664  0.025637
4            (22865)        667  0.025753
..               ...        ...       ...
115          (20725)       1608  0.062085
116          (47566)       1706  0.065869
117         (85099B)       2135  0.082432
118          (22423)       2172  0.083861
119         (85123A)       2246  0.086718

[120 rows x 3 columns]

In [16]:
print(freq_pat.to_string(),'\n')

    Frequent Pattern  Frequency   Support
0            (22114)        652  0.025174
1            (22969)        654  0.025251
2            (22835)        663  0.025598
3            (21213)        664  0.025637
4            (22865)        667  0.025753
5            (21915)        671  0.025907
6            (23208)        672  0.025946
7            (79321)        673  0.025985
8            (20713)        674  0.026023
9            (22966)        674  0.026023
10           (22907)        676  0.026100
11           (22551)        681  0.026293
12           (85152)        682  0.026332
13           (84378)        689  0.026602
14           (22662)        690  0.026641
15           (22385)        692  0.026718
16           (82484)        696  0.026873
17           (84380)        696  0.026873
18           (20685)        704  0.027181
19           (21930)        708  0.027336
20           (22554)        709  0.027375
21             (DOT)        710  0.027413
22           (22467)        714  0

***ASSOCIATION RULES***

In [17]:
association_rules = pd.DataFrame(assoc_rules,columns = ['Antecedent','Consequent','Support','Confidence'])
print('THE ASSOCIATION RULES FOR min_support =',support,'AND min_confidence =',confidence,'ARE THE FOLLOWING')
print('THE ASSOCIATION RULE IS TO BE READ AS "Antecedent => Consequent" WITH RESPECTIVE SUPPORT AND CONFIDENCE')
association_rules

THE ASSOCIATION RULES FOR min_support = 0.025 AND min_confidence = 0.4 ARE THE FOLLOWING
THE ASSOCIATION RULE IS TO BE READ AS "Antecedent => Consequent" WITH RESPECTIVE SUPPORT AND CONFIDENCE


Antecedent Consequent   Support  Confidence
0    {22697}    {22699}  0.030270    0.741722
1    {22699}    {22697}  0.030270    0.700000
2    {22411}   {85099B}  0.026371    0.575400
3    {21931}   {85099B}  0.028301    0.610325
4    {22386}   {85099B}  0.032162    0.676686
5    {20727}    {20725}  0.025019    0.500386
6    {20725}    {20727}  0.025019    0.402985
7    {22383}    {20725}  0.025598    0.507657
8    {20725}    {22383}  0.025598    0.412313

In [18]:
print(association_rules.to_string())

  Antecedent Consequent   Support  Confidence
0    {22697}    {22699}  0.030270    0.741722
1    {22699}    {22697}  0.030270    0.700000
2    {22411}   {85099B}  0.026371    0.575400
3    {21931}   {85099B}  0.028301    0.610325
4    {22386}   {85099B}  0.032162    0.676686
5    {20727}    {20725}  0.025019    0.500386
6    {20725}    {20727}  0.025019    0.402985
7    {22383}    {20725}  0.025598    0.507657
8    {20725}    {22383}  0.025598    0.412313
